## Code from OntoZSL

### Combining the entities and relations embeddings into one

In [1]:
# numpy data L2 normalization
import os
import json
import sys
import pickle as pkl
import numpy as np
import scipy.io as scio
from pathlib import Path


def loadDict(file_name):
    entities = list()
    wnids = open(file_name, 'r')
    try:
        for line in wnids:
            line = line[:-1]
            index, cls = line.split('\t')
            entities.append(cls)
    finally:
        wnids.close()
    print(len(entities))
    return entities



datadir = 'data'
dataset = 'ontology'

DATASET_DIR = os.path.join(datadir, dataset)
DATA_DIR = DATASET_DIR


entity_file = os.path.join(DATA_DIR, 'entities_names.dict')
relation_file = os.path.join(DATA_DIR, 'relations.dict')


# load entity dict
entities = loadDict(entity_file)
relations = loadDict(relation_file)

embed_dir = os.path.join(DATA_DIR, 'save_onto_embeds')

ent_embed_file = embed_dir + '/entity_1000.npy'
rel_embed_file = embed_dir + '/relation_1000.npy'

ent_embeds = np.load(ent_embed_file)
print(ent_embeds.shape)

rel_embeds = np.load(rel_embed_file)
print(rel_embeds.shape)

embed_dict = dict()
for i, ent in enumerate(entities):
    embed_dict[ent] = ent_embeds[i].astype('float32')
for i, rel in enumerate(relations):
    embed_dict[rel] = rel_embeds[i].astype('float32')

print(len(embed_dict.keys()))


Path(DATA_DIR + '/embeddings').mkdir(parents=True, exist_ok=True)
save_name = open(os.path.join(DATA_DIR, 'embeddings', 'Onto_TransE.pkl'), 'wb')
pkl.dump(embed_dict, save_name)



124749
5
(124749, 100)
(5, 100)
124597


### Getting the textual embedding for each entity

In [2]:
# -*- coding: utf-8 -*-
import sys, os, re
import numpy as np
from collections import namedtuple, defaultdict
from itertools import count
from copy import deepcopy

import pickle
import json
from PIL import ImageFile
import codecs

import io
import requests
from PIL import Image
from torchvision import models, transforms
from torch.autograd import Variable

from nltk.corpus import stopwords
import string
from sklearn import feature_extraction
from sklearn.feature_extraction.text import TfidfTransformer, TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer


def get_embedding(entity_str, word_vectors, get_vector):
    try:
        feat = get_vector(word_vectors, entity_str)
        return feat
    except:
        feat = np.zeros(WORD_VEC_LEN)

    str_set = filter(None, re.split("[ \-_]+", entity_str))
    str_set = list(str_set)
    cnt_word = 0
    for i in range(len(str_set)):
        temp_str = str_set[i]
        try:
            now_feat = get_vector(word_vectors, temp_str)
            feat = feat + now_feat
            cnt_word = cnt_word + 1
        except:
            continue

    if cnt_word > 0:
        feat = feat / cnt_word
    return feat


def generate_text_embedding(ent2doc):

    # all_feats = list()

    has = 0
    cnt_missed = 0
    missed_list = []
    entities2vec = dict()
    for ent, doc in ent2doc.items():
        feat = np.zeros(shape=WORD_VEC_LEN, dtype='float32')

        doc = doc.replace('_', ' ')
        doc = doc.replace('-', ' ')
        # print(doc)

        options = doc.split()
        cnt_word = 0

        for option in options:
            now_feat = get_embedding(option.strip(), word_vectors, get_vector)
            if np.abs(now_feat.sum()) > 0:
                cnt_word += 1
                feat += now_feat
        if cnt_word > 0:
            feat = feat / cnt_word

        if cnt_word != len(options):
            print(ent, 'count:', cnt_word)

        if np.abs(feat.sum()) == 0:
            # print('cannot find word ' + class_name)
            cnt_missed = cnt_missed + 1
            missed_list.append(ent + "###" + doc)
            feat = feat

        else:
            has += 1
            feat = feat / (np.linalg.norm(feat) + 1e-6)

        # all_feats.append(feat)
            entities2vec[ent] = feat


    # all_feats = np.array(all_feats)
    # print(all_feats.shape)
    for each in missed_list:
        print(each)
    print('does not have semantic embedding: ', cnt_missed, 'has: ', has)


    return entities2vec
    # entities2vec = dict()
    # for i, ent in enumerate(ent_list):
    #     entities2vec[ent] = ent_matrix[i]
    #     # print(ent_matrix[i])
    #
    # return entities2vec



def glove_google(word_vectors, word):
    return word_vectors[word]

def get_glove_dict(txt_dir):
    print('load glove word embedding')
    txt_file = os.path.join(txt_dir, 'glove.6B.300d.txt')
    word_dict = {}
    feat = np.zeros(WORD_VEC_LEN)
    with open(txt_file) as fp:
        for line in fp:
            words = line.split()
            assert len(words) - 1 == WORD_VEC_LEN
            for i in range(WORD_VEC_LEN):
                feat[i] = float(words[i+1])
            feat = np.array(feat)
            word_dict[words[0]] = feat
    print('loaded to dict!')
    return word_dict


def readTxt(file_name):
    class_list = list()
    wnids = open(file_name, 'r')
    try:
        for line in wnids:
            line = line[:-1]
            class_list.append(line)
    finally:
        wnids.close()
    print(len(class_list))
    return class_list

def load_class():
    seen = readTxt(seen_file)
    unseen = readTxt(unseen_file)
    return seen, unseen

def loadDict(file_name):
    entities = list()
    wnids = open(file_name, 'r')
    try:
        for line in wnids:
            line = line[:-1]
            index, cls = line.split('\t')
            entities.append(cls)
    finally:
        wnids.close()
    print(len(entities))
    return entities

def load_domain_range(triples_file):
    text_file = codecs.open(triples_file, "r", "utf-8")
    lines = text_file.readlines()
    triples = list()
    for line in lines:
        line_arr = line.rstrip("\r\n").split("\t")
        head = line_arr[0]
        rel = line_arr[1]
        tail = line_arr[2]
        triples.append((head, rel, tail))
    return triples


datadir = 'data'
dataset = 'ontology'

WORD_VEC_LEN = 300
word_vectors = get_glove_dict('data/glove')
get_vector = glove_google

DATASET_DIR = os.path.join(datadir, dataset)
DATA_DIR = DATASET_DIR



entity_text_file = os.path.join(DATA_DIR, 'entities_names.dict')
entity_file = os.path.join(DATA_DIR, 'entities.dict')
triples_file = os.path.join(DATA_DIR, 'triples_names.txt')


entities = loadDict(entity_file)
entities_names = loadDict(entity_text_file)



ent2doc = dict()
with open(entity_text_file) as f_doc:
    lines = f_doc.readlines()

    for i in range(len(lines)):
        entity_text = lines[i].strip().split('\t')[1].strip()
        ent2doc[entity_text] = entity_text


entities2vec = generate_text_embedding(ent2doc)
print(len(entities2vec.keys()))


save_name = open(os.path.join(DATA_DIR, 'embeddings', 'Onto_Text_Embed.pkl'), 'wb')
pickle.dump(entities2vec, save_name)



/home/leopold/Documents/4A/stage/onto_cgans/venv/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


load glove word embedding
loaded to dict!
124749
124749
orphacode count: 0
alexander_disease_and_hyperreflexia_very_frequent_association count: 6
alexander_disease_and_megalencephaly_very_frequent_association count: 6
alexander_disease_and_depressivity_frequent_association count: 5
alexander_disease_and_dysphasia_frequent_association count: 5
alexander_disease_and_recurrent_singultus_frequent_association count: 6
alexander_disease_and_aqueductal_stenosis_occasional_association count: 6
alexander_disease_and_hyperlordosis_occasional_association count: 5
alexander_disease_and_hyperpigmented_nevi_occasional_association count: 6
alpha-mannosidosis_and_macroglossia_very_frequent_association count: 5
alpha-mannosidosis_and_coarse_facial_features_very_frequent_association count: 8
alpha-mannosidosis_and_hearing_impairment_very_frequent_association count: 7
alpha-mannosidosis_and_cataract_very_frequent_association count: 6
alpha-mannosidosis_and_intellectual_disability_very_frequent_associatio

oculocerebrorenal_syndrome_of_lowe_and_nystagmus_very_frequent_association count: 8
oculocerebrorenal_syndrome_of_lowe_and_amblyopia_very_frequent_association count: 8
oculocerebrorenal_syndrome_of_lowe_and_carious_teeth_occasional_association count: 7
oculocerebrorenal_syndrome_of_lowe_and_dental_crowding_occasional_association count: 8
oculocerebrorenal_syndrome_of_lowe_and_taurodontia_occasional_association count: 6
oculocerebrorenal_syndrome_of_lowe_and_abnormality_of_dental_enamel_occasional_association count: 10
oculocerebrorenal_syndrome_of_lowe_and_delayed_eruption_of_teeth_occasional_association count: 10
oculocerebrorenal_syndrome_of_lowe_and_periodontitis_occasional_association count: 7
oculocerebrorenal_syndrome_of_lowe_and_depressivity_very_frequent_association count: 7
oculocerebrorenal_syndrome_of_lowe_and_obsessive-compulsive_behavior_frequent_association count: 9
oculocerebrorenal_syndrome_of_lowe_and_stereotypy_very_frequent_association count: 7
oculocerebrorenal_synd

holoprosencephaly_and_panhypopituitarism_occasional_association count: 4
holoprosencephaly_and_brachydactyly_occasional_association count: 4
holoprosencephaly_and_omphalocele_occasional_association count: 4
holoprosencephaly_and_talipes_occasional_association count: 4
holoprosencephaly_and_encephalocele_occasional_association count: 4
holoprosencephaly_and_hyposmia_frequent_association count: 4
holoprosencephaly_and_joint_hyperflexibility_occasional_association count: 5
holoprosencephaly_and_aplasia/hypoplasia_of_the_lungs_occasional_association count: 7
holoprosencephaly_and_aplasia/hypoplasia_of_the_cerebellum_occasional_association count: 7
holoprosencephaly_and_aplasia/hypoplasia_of_the_corpus_callosum_frequent_association count: 8
holoprosencephaly_and_abnormality_of_the_antihelix_occasional_association count: 7
holoprosencephaly_and_cyclopia_frequent_association count: 4
holoprosencephaly_and_aplasia/hypoplasia_involving_the_nose_occasional_association count: 7
holoprosencephaly_

isolated_glycerol_kinase_deficiency_and_hyperlordosis_frequent_association count: 7
multiple_carboxylase_deficiency_and_abnormal_enzyme/coenzyme_activity_very_frequent_association count: 9
multiple_carboxylase_deficiency_and_decreased_biotinidase_activity_frequent_association count: 8
multiple_carboxylase_deficiency_and_spastic_paraparesis_very_rare_association count: 8
neonatal_severe_primary_hyperparathyroidism_and_abnormality_of_the_metaphysis_very_frequent_association count: 11
neonatal_severe_primary_hyperparathyroidism_and_aminoaciduria_very_frequent_association count: 8
hypogonadism-mitral_valve_prolapse-intellectual_disability_syndrome_and_downslanted_palpebral_fissures_frequent_association count: 12
hypogonadism-mitral_valve_prolapse-intellectual_disability_syndrome_and_intellectual_disability,_mild_very_frequent_association count: 13
congenital_diaphragmatic_hernia_and_intestinal_malrotation_frequent_association count: 7
congenital_diaphragmatic_hernia_and_aplasia/hypoplasia_

...

marcus-gunn_syndrome_and_marcus_gunn_jaw_winking_synkinesis_obligate_association count: 10
marcus-gunn_syndrome_and_hypotropia_frequent_association count: 6
marcus-gunn_syndrome_and_anisometropia_occasional_association count: 6
marcus-gunn_syndrome_and_superior_rectus_muscle_underaction_occasional_association count: 9
marcus-gunn_syndrome_and_choanal_atresia_very_rare_association count: 8
marcus-gunn_syndrome_and_nephrolithiasis_very_rare_association count: 7
primary_intestinal_lymphangiectasia_and_edema_very_frequent_association count: 7
primary_intestinal_lymphangiectasia_and_anemia_very_frequent_association count: 7
primary_intestinal_lymphangiectasia_and_intestinal_lymphangiectasia_very_frequent_association count: 7
primary_intestinal_lymphangiectasia_and_combined_immunodeficiency_very_frequent_association count: 8
primary_intestinal_lymphangiectasia_and_functional_abnormality_of_the_gastrointestinal_tract_very_frequent_association count: 12
primary_intestinal_lymphangiectasia_and_

camptodactyly_of_finger count: 2
visceral_angiomatosis count: 1
male_pseudohermaphroditism count: 1
aplasia/hypoplasia_of_the_phalanges_of_the_hallux count: 6
multiple_lentigines count: 1
melanonychia count: 0
synostosis_of_carpal_bones count: 3
multicystic_kidney_dysplasia count: 2
clitoromegaly count: 0
wide_anterior_fontanel count: 2
brushfield_spots count: 1
polymicrogyria count: 0
tracheomalacia count: 0
rectovaginal_fistula count: 1
epibulbar_dermoid count: 1
triphalangeal_thumb count: 1
toe_clinodactyly count: 1
rectoperineal_fistula count: 1
aplasia/hypoplasia_of_the_3rd_toe count: 4
synophrys count: 0
hamartomatous_polyposis count: 1
adenoma_sebaceum count: 1
papule count: 0
abnormal_diaphysis_morphology count: 2
aplasia/hypoplasia_of_the_corpus_callosum count: 4
pseudoepiphyses_of_the_metacarpals count: 3
ureteropelvic_junction_obstruction count: 2
proximal_radio-ulnar_synostosis count: 3
abnormality_of_the_antihelix count: 3
choroideremia count: 0
hemihypertrophy count: 0
om

lipemia_retinalis count: 0
autoimmune_hypoparathyroidism count: 1
calcium_nephrolithiasis count: 1
hyperostosis_frontalis_interna count: 2
osteoma_cutis count: 1
diaphyseal_sclerosis count: 1
cortical_subperiosteal_resorption_of_humeral_metaphyses count: 4
periauricular_skin_pits count: 2
aplasia/hypoplasia_of_the_spleen count: 3
non-caseating_epithelioid_cell_granulomatosis count: 4
elevated_gamma-glutamyltransferase_activity count: 3
elevated_carcinoembryonic_antigen_level count: 3
elevated_serum_11-deoxycortisol count: 3
primary_hypercortisolism count: 1
midgut_malrotation count: 1
appendiceal_mucinous_neoplasm count: 2
ovoid_thoracolumbar_vertebrae count: 2
generalized_keratosis_follicularis count: 2
conjunctival_hyperemia count: 1
subcapsular_cataract count: 1
central_opacification_of_the_cornea count: 4
thinning_of_descemet_membrane count: 3
fifth_finger_distal_phalanx_clinodactyly count: 4
aplasia/hypoplasia_of_the_scapulae count: 3
bilateral_microphthalmos count: 1
decreased_si

camptodactyly-taurinuria_syndrome count: 1
camptodactyly-joint_contractures-facial_skeletal_defects_syndrome count: 6
camptobrachydactyly count: 0
night_blindness-skeletal_anomalies-dysmorphism_syndrome count: 5
cerebrocostomandibular_syndrome count: 1
catel-manzke_syndrome count: 2
cataract-microcornea_syndrome count: 2
cataract-aberrant_oral_frenula-growth_delay_syndrome count: 6
hereditary_hyperferritinemia-cataract_syndrome count: 3
carnosinase_deficiency count: 1
böök_syndrome count: 1
tricho-retino-dento-digital_syndrome count: 2
borjeson-forssman-lehmann_syndrome count: 2
bonnemann-meinecke-reich_syndrome count: 3
blepharoptosis-myopia-ectopia_lentis_syndrome count: 2
metaphyseal_acroscyphodysplasia count: 0
blepharonasofacial_malformation_syndrome count: 2
maxillonasal_dysplasia count: 1
auriculoosteodysplasia count: 0
congenital_contractural_arachnodactyly count: 1
beemer-ertbruggen_syndrome count: 2
distal_limb_deficiencies-micrognathia_syndrome count: 4
infantile_choroidocer

galactose_mutarotase_deficiency count: 2
blepharophimosis-ptosis-epicanthus_inversus_syndrome_plus count: 4
exstrophy-epispadias_complex count: 1
dyggve-melchior-clausen_disease count: 3
otospondylomegaepiphyseal_dysplasia count: 1
progressive_pseudorheumatoid_arthropathy_of_childhood count: 3
osteochondrosis_of_the_metatarsal_bone count: 4
triglyceride_deposit_cardiomyovasculopathy count: 2
primary_biliary_cholangitis/primary_sclerosing_cholangitis_and_autoimmune_hepatitis_overlap_syndrome count: 9
osteochondrosis_of_the_tarsal_bone count: 4
resistance_to_thyrotropin-releasing_hormone_syndrome count: 5
livedoid_vasculopathy count: 0
familial_thyroid_dyshormonogenesis count: 2
necrobiosis_lipoidica count: 0
krt1-related_diffuse_nonepidermolytic_keratoderma count: 3
mirizzi_syndrome count: 1
aquagenic_palmoplantar_keratoderma count: 2
extracranial_carotid_artery_aneurysm count: 3
severe_primary_trimethylaminuria count: 2
neonatal_alloimmune_neutropenia count: 2
isolated_splenogonadal_fu

### Processing triples (hrt to htr)

In [3]:
datadir = 'data'
dataset = 'ontology'

DATASET_DIR = os.path.join(datadir, dataset)
DATA_DIR = DATASET_DIR

triples_file = os.path.join(DATA_DIR, 'triples_names.txt')
save_file = os.path.join(DATA_DIR, 'triples_names_htr.txt')

wr_fp = open(save_file, 'w')
text_file = codecs.open(triples_file, "r", "utf-8")
lines = text_file.readlines()
for line in lines:
    line_arr = line.rstrip("\r\n").split("\t")
    head = line_arr[0]
    rel = line_arr[1]
    tail = line_arr[2]

    wr_fp.write('%s\t%s\t%s\n' % (head, tail, rel))

wr_fp.close()

### Model training for text-aware embedding (PyTorch)

In [5]:
# imports
import argparse
import os
import pickle
import pandas as pd
import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, Dataset
from torchvision.transforms import ToTensor

In [8]:
class TrainDataSet(Dataset):
    
    def __init__(self, data_dir, struct_embeds_fn, word_embeds_fn, triples_fn, entities_fn, entities_names_fn):
        with open(os.path.join(data_dir, 'embeddings', struct_embeds_fn), 'rb') as f:
            self.struct_embeds = pickle.load(f)
        with open(os.path.join(data_dir, 'embeddings', word_embeds_fn), 'rb') as f:
            self.word_embeds = pickle.load(f)
        
        self.triples = []
        with open(os.path.join(data_dir, triples_fn)) as f:
            for line in f:
                h, t,r = line.strip().split('\t')
                self.triples.append((h, t, r))
        self.triples_set = set(self.triples)
        
        self.entities = []
        with open(os.path.join(data_dir, entities_fn)) as f:
            for line in f:
                eid, entity = line.strip().split('\t')
                self.entities.append((eid, entity))
                
        self.entities_names = []
        with open(os.path.join(data_dir, entities_names_fn)) as f:
            for line in f:
                eid, entity = line.strip().split('\t')
                self.entities_names.append((eid, entity))
                
        temp_triples = []
        for (h, t, r) in self.triples:
            if h in self.struct_embeds and h in self.word_embeds and \
                t in self.struct_embeds and t in self.word_embeds:
                temp_triples.append((h, t, r))
        self.triples = temp_triples
        
        temp_entities_names = []
        for (eid, e) in self.entities_names:
            if e in self.struct_embeds and e in self.word_embeds:
                temp_entities_names.append((eid, e))
        self.entities_names = temp_entities_names
        
        
        """self.triples = pd.read_csv(os.path.join(data_dir, triples_fn), sep='\t', names=['head', 'tail', 'relation'])
        self.entities = pd.read_csv(os.path.join(data_dir, entities_fn), sep='\t', names=['id', 'entity'])
        self.entities_names = pd.read_csv(os.path.join(data_dir, entities_names_fn), sep='\t', names=['id', 'entity'])
        
        
        # filtering out triples that don't have a full structural or word embedding
        self.triples = self.triples.loc[self.triples['head'].isin(self.struct_embeds) &
                                        self.triples['head'].isin(self.word_embeds)]
        self.triples = self.triples.loc[self.triples['tail'].isin(self.struct_embeds) &
                                        self.triples['tail'].isin(self.word_embeds)]
        # filtering out entities the same way
        self.entities_names = self.entities_names.loc[self.entities_names['entity'].isin(self.struct_embeds) & 
                                                      self.entities_names['entity'].isin(self.word_embeds)]"""
        
        self.transform = torch.tensor


    def __len__(self):
        return len(self.triples)

    def __getitem__(self, idx):
        pos_triple = self.triples[idx]
        neg_triple_head = self.sample_negative_head(pos_triple)
        neg_triple_tail = self.sample_negative_tail(pos_triple,)

        return (self.transform(self.struct_embeds[pos_triple[0]]), self.transform(self.word_embeds[pos_triple[0]]), 
                self.transform(self.struct_embeds[pos_triple[1]]), self.transform(self.struct_embeds[pos_triple[2]]), self.word_embeds[pos_triple[2]], 
                self.transform(self.struct_embeds[neg_triple_head[0]]), 
                self.transform(self.word_embeds[neg_triple_head[0]]), 
                self.transform(self.struct_embeds[neg_triple_tail[1]]), 
                self.transform(self.word_embeds[neg_triple_tail[1]]))
    
    def sample_negative_head(triple_to_corrupt):
        for i in range(len(self.entities)):
            index = np.random.randint(0, len(entity_list))
            random_entity = self.entities_names[index]
            if random_entity != triples_to_corrupt[0]:
                negative_triple = (random_entity, triple_to_corrupt[1], triple_to_corrupt[2])
                if negative_triple not in self.triples:
                    return new_triple
        negative_triple = (triple_to_corrupt[1], triple_to_corrupt[1], triple_to_corrupt[2])
        return negative_triple
    
    def sample_negative_tail(triple_to_corrupt):
        for i in range(len(self.entities)):
            index = np.random.randint(0, len(entity_list))
            random_entity = self.entities_names[index]
            if random_entity != triples_to_corrupt[1]:
                negative_triple = (triple_to_corrupt[0], random_entity, triple_to_corrupt[2])
                if negative_triple not in self.triples:
                    return new_triple
        negative_triple = (triple_to_corrupt[0], triple_to_corrupt[0], triple_to_corrupt[2])
        return negative_triple


class EmbeddingModel(nn.Module):
    
    def __init__(self, dropout_rate=0.25, in_size=100, out_size=100):
        super(EmbeddingModel, self).__init__()
        self.rel = nn.Linear(in_size, out_size)
        self.fc_head_struct_pos = nn.Linear(in_size, out_size)
        self.fc_head_struct_neg = nn.Linear(in_size, out_size)
        self.fc_head_text_pos = nn.Linear(in_size, out_size)
        self.fc_head_text_neg = nn.Linear(in_size, out_size)
        self.fc_tail_struct_pos = nn.Linear(in_size, out_size)
        self.fc_tail_struct_neg = nn.Linear(in_size, out_size)
        self.fc_tail_text_pos = nn.Linear(in_size, out_size)
        self.fc_tail_text_neg = nn.Linear(in_size, out_size)
        self.dropout = nn.Dropout(dropout_rate)
        
    def forward(self, rel, head_struct_pos, tail_struct_pos, head_text_pos, tail_text_pos, 
              head_struct_neg, tail_struct_neg, head_text_neg, tail_text_neg):
        rel = self.dropout(F.relu(self.rel(rel)))
        hsp = self.dropout(F.relu(self.fc_head_struct_pos(head_struct_pos)))
        htp = self.dropout(F.relu(self.fc_head_text_pos(head_text_pos)))
        hsn = self.dropout(F.relu(self.fc_head_struct_neg(head_struct_neg)))
        htn = self.dropout(F.relu(self.fc_head_text_neg(head_text_neg)))
        tsp = self.dropout(F.relu(self.fc_tail_struct_pos(tail_struct_pos)))
        ttp = self.dropout(F.relu(self.fc_tail_text_pos(tail_text_pos)))
        tsn = self.dropout(F.relu(self.fc_tail_struct_neg(tail_struct_neg)))
        ttn = self.dropout(F.relu(self.fc_tail_text_neg(tail_text_neg)))

        return rel, hsp, tsp, htp, ttp, hsn, tsn, htn, ttn
    
    def score(self, rel, head_struct_pos, tail_struct_pos, head_text_pos, tail_text_pos, 
              head_struct_neg, tail_struct_neg, head_text_neg, tail_text_neg):
        # head
        head_fs_pos = torch.sum(abs(head_struct_pos + rel - tail_struct_pos), 1, keepdim=True)
        head_fs_neg = torch.sum(abs(head_struct_pos + rel - tail_struct_neg), 1, keepdim=True)
        
        head_fts_pos = torch.sum(abs(head_text_pos + rel - tail_struct_pos), 1, keepdim=True)
        head_fts_neg = torch.sum(abs(head_text_pos + rel - tail_struct_neg), 1, keepdim=True)
        
        head_fst_pos = torch.sum(abs(head_struct_pos + rel - tail_text_pos), 1, keepdim=True)
        head_fst_neg = torch.sum(abs(head_struct_pos + rel - tail_text_neg), 1, keepdim=True)

        head_ft_pos = torch.sum(abs(head_text_pos + rel - tail_text_pos), 1, keepdim=True)
        head_ft_neg = torch.sum(abs(head_text_pos + rel - tail_text_neg), 1, keepdim=True)
        
        head_fadd_pos = torch.sum(abs((head_struct_pos + head_text_pos) 
                                      + rel - (tail_struct_pos + tail_text_pos)), 1, keepdim=True)
        head_fadd_neg = torch.sum(abs((head_struct_pos + head_text_pos) 
                                      + rel - (tail_struct_neg + tail_text_neg)), 1, keepdim=True)
        
        head_ftotal_pos = torch.sum([head_fs_pos, head_fts_pos, head_fst_pos, 
                                     head_ft_pos, head_fadd_pos], 0, keepdim=False)
        head_ftotal_neg = torch.sum([head_fs_neg, head_fts_neg, head_fst_neg, 
                                     head_ft_neg, head_fadd_neg], 0, keepdim=False)
        
        # tail
        tail_fs_pos = torch.sum(abs(tail_struct_pos - rel - head_struct_pos), 1, keepdim=True)
        tail_fs_neg = torch.sum(abs(tail_struct_pos - rel - head_struct_neg), 1, keepdim=True)
        
        tail_fts_pos = torch.sum(abs(tail_text_pos - rel - head_struct_pos), 1, keepdim=True)
        tail_fts_neg = torch.sum(abs(tail_text_pos - rel - head_struct_neg), 1, keepdim=True)
        
        tail_fst_pos = torch.sum(abs(tail_struct_pos - rel - head_text_pos), 1, keepdim=True)
        tail_fst_neg = torch.sum(abs(tail_struct_pos - rel - head_text_neg), 1, keepdim=True)

        tail_ft_pos = torch.sum(abs(tail_text_pos - rel - head_text_pos), 1, keepdim=True)
        tail_ft_neg = torch.sum(abs(tail_text_pos - rel - head_text_neg), 1, keepdim=True)
        
        tail_fadd_pos = torch.sum(abs((tail_struct_pos + tail_text_pos) 
                                      - rel - (head_struct_pos + head_text_pos)), 1, keepdim=True)
        tail_fadd_neg = torch.sum(abs((tail_struct_pos + tail_text_pos) 
                                      - rel - (head_struct_neg + head_text_neg)), 1, keepdim=True)
        
        tail_ftotal_pos = torch.sum([tail_fs_pos, tail_fts_pos, tail_fst_pos, 
                                     tail_ft_pos, tail_fadd_pos], 0, keepdim=False)
        tail_ftotal_neg = torch.sum([tail_fs_neg, tail_fts_neg, tail_fst_neg, 
                                     tail_ft_neg, tail_fadd_neg], 0, keepdim=False)
        
        return head_ftotal_pos, head_ftotal_neg, tail_ftotal_pos, tail_ftotal_neg
    
    def loss(self, margin, rel, head_struct_pos, tail_struct_pos, head_text_pos, tail_text_pos, 
              head_struct_neg, tail_struct_neg, head_text_neg, tail_text_neg):
        rel, hsp, tsp, htp, ttp, hsn, tsn, htn, ttn = data
        score_head_pos, score_head_neg, score_tail_pos, score_tail_neg = self.score(rel, head_struct_pos, 
                                                                                    tail_struct_pos, head_text_pos, 
                                                                                    tail_text_pos, head_struct_neg, 
                                                                                    tail_struct_neg, head_text_neg, 
                                                                                    tail_text_neg)
        loss_1 = torch.maximum(0., margin - score_head_neg + score_head_pos)
        loss_2 = torch.maximum(0., margin - score_tail_neg + score_tail_pos)
        return loss_1 + loss_2

Using cpu device


In [9]:
parser = argparse.ArgumentParser()
parser.add_argument('--data_dir', default='data/ontology', help='')
parser.add_argument('--struct_embeds_fn', default='Onto_TransE.pkl', help='')
parser.add_argument('--word_embeds_fn', default='Onto_Text_Embed.pkl', help='')
parser.add_argument('--triples_fn', default='triples_names_htr.txt', help='')
parser.add_argument('--entities_fn', default='entities.dict', help='')
parser.add_argument('--entities_names_fn', default='entities_names.dict', help='')
parser.add_argument('--rel_str_embed', default=100, type=int, help='relation structural embeddings size')
parser.add_argument('--ent_str_embed', default=100, type=int, help='entity structural embeddings size')
parser.add_argument('--ent_text_embed', default=300, type=int, help='entity textual embeddings size')
parser.add_argument('--mapping_size', default=100, type=int, help='hidden layer size')
parser.add_argument('--dropout_ratio', default=0.5, type=float, help='')
parser.add_argument('--margin', default=10, type=int, help='')
parser.add_argument('--training_epochs', default=10, type=int, help='')
parser.add_argument('--batch_size', default=100, type=int, help='')
parser.add_argument('--display_loss_step', default=100, type=int, help='')
parser.add_argument('--initial_learning_rate', default=0.001, type=float, help='')
parser.add_argument('--activation_function', default='', help='')
param = parser.parse_args([])

# Get cpu or gpu device for training.
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

# Set fixed random number seed
torch.manual_seed(42)

training_data = TrainDataSet(param.data_dir, param.struct_embeds_fn, param.word_embeds_fn, param.triples_fn,
                            param.entities_fn, param.entities_names_fn)
train_dataloader = DataLoader(training_data, batch_size=param.batch_size, shuffle=True)

model = EmbeddingModel().to(device)

# loss_function 

current_learning_rate = param.initial_learning_rate
optimizer = torch.optim.Adam(model.parameters(), lr=current_learning_rate)

initial_valid_loss = 100

# Run the training loop
for epoch in range(param.training_epochs):

    # Print epoch
    print(f'Starting epoch {epoch+1}')
    
    # Set current loss value
    training_loss = 0.0
    
    # Iterate over the DataLoader for training data
    for i, data in enumerate(train_dataloader, 0):
      
        # Get inputs
        data = data.to(device)

        # Zero the gradients
        optimizer.zero_grad()

        # Perform forward pass
        outputs = model(data)

        # Compute loss
        loss = model.loss(param.margin, outputs)

        # Perform backward pass
        loss.backward()

        # Perform optimization
        optimizer.step()

        # Print statistics
        current_loss += loss.item()
        if i % display_loss_step == display_loss_step-1:
          print('Loss after mini-batch %5d: %.3f' %
                (i + 1, current_loss / 500))
          current_loss = 0.0

EmbeddingModel(
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (linear_relu_stack): Sequential(
    (0): Linear(in_features=784, out_features=512, bias=True)
    (1): ReLU()
    (2): Linear(in_features=512, out_features=512, bias=True)
    (3): ReLU()
    (4): Linear(in_features=512, out_features=10, bias=True)
  )
)


In [14]:
# look at generation of head and tail positive samples
# data connection between model call with inputs and forward function